# Inhaltsbasiertes Empfehlungssystem mit KNN-Klassifikation

## Schritt 1: Einschränken der Daten und Festlegen des Nutzers

Zunächst bestimmen wir den Nutzer, für den unser inhaltsbasiertes Filmempfehlungssystem trainiert werden soll.<br/>
Erinnerung: Inhaltsbasierte Empfehlungssysteme berechnen Empfehlungen in Abhängigkeit der Filminhalte und den Informationen zu einem einzigen Nutzer!

In [2]:
nutzer = 1

## Schritt 2: Datensatzvorbereitung

Wie genau der Datensatz vorbereitet wird findest du in Kapitel 14.5.1.2.

In [3]:
import pandas as pd
import re

ratings = pd.read_csv(r'ratings.csv',encoding='latin-1')
movies = pd.read_csv(r'movies.csv',encoding='latin-1')

movies_filter = movies[movies['movieId']<1000]
for elem in movies_filter['genres'].str.split(pat = '|', expand = False).explode().unique():
    column = []
    for i in range(len(movies_filter)):
        if elem in movies_filter['genres'].str.split(pat = '|', expand = False)[i]:
            column.append(1)
        else:
            column.append(0)
    movies_filter[elem] = column
movies_filter = movies_filter.drop(['title','genres'], axis='columns')

ratings_user = ratings[ratings['userId']==nutzer]
total_user = pd.merge(movies_filter,ratings_user,left_on=['movieId'],
              right_on=['movieId'],
              how='inner').drop(['userId'], axis='columns')
total_user

movieId  Action  Adventure  Sci-Fi  IMAX  Children  Comedy  Fantasy  \
0         4       0          1       0     1         1       1        1   
1         7       0          1       0     0         1       0        0   
2         8       0          0       0     0         0       1        0   
3         9       0          1       0     0         1       1        0   
4        10       1          1       0     0         0       0        1   
5        12       0          1       0     0         1       1        1   
6        14       0          0       0     0         0       1        0   
7        17       0          0       0     0         0       1        0   
8        18       0          1       0     0         1       1        0   
9        22       0          0       0     0         1       1        0   
10       23       0          1       0     1         1       0        0   
11       24       1          1       1     0         0       0        0   
12       27       0          0       0     0         0       0        0   

    Animation  Romance  Drama  War  Crime  Thriller  Musical  rating  
0           0        0      0    0      0         0        0     4.0  
1           0        1      0    0      0         0        0     5.0  
2           0        0      0    0      0         0        0     4.0  
3           1        0      0    0      0         0        0     5.0  
4           0        0      0    0      0         0        0     3.0  
5           1        0      0    0      0         0        0     4.0  
6           0        0      0    0      1         0        0     4.0  
7           0        0      1    0      0         0        0     5.0  
8           1        0      0    0      0         0        0     5.0  
9           0        0      0    0      0         0        0     5.0  
10          1        0      1    0      0         0        1     5.0  
11          0        0      0    0      0         1        0     4.0  
12          0        1      1    0      0         0        0     5.0

## Schritt 3: Klassen und Attribute angeben

Um unser Modell zu trainieren, müssen wir dem Modell sagen, welches die Attribute und welches die Klassen sind, die es vorhersagen soll. Dafür trennen wir den DataFrame in die Attribute, d.h. alle Genre Spalten, und die Klasse, die Spalte ratings.

In [4]:
X = total_user.drop(['rating','movieId'], axis='columns')
y = total_user.rating
X

Action  Adventure  Sci-Fi  IMAX  Children  Comedy  Fantasy  Animation  \
0        0          1       0     1         1       1        1          0   
1        0          1       0     0         1       0        0          0   
2        0          0       0     0         0       1        0          0   
3        0          1       0     0         1       1        0          1   
4        1          1       0     0         0       0        1          0   
5        0          1       0     0         1       1        1          1   
6        0          0       0     0         0       1        0          0   
7        0          0       0     0         0       1        0          0   
8        0          1       0     0         1       1        0          1   
9        0          0       0     0         1       1        0          0   
10       0          1       0     1         1       0        0          1   
11       1          1       1     0         0       0        0          0   
12       0          0       0     0         0       0        0          0   

    Romance  Drama  War  Crime  Thriller  Musical  
0         0      0    0      0         0        0  
1         1      0    0      0         0        0  
2         0      0    0      0         0        0  
3         0      0    0      0         0        0  
4         0      0    0      0         0        0  
5         0      0    0      0         0        0  
6         0      0    0      1         0        0  
7         0      1    0      0         0        0  
8         0      0    0      0         0        0  
9         0      0    0      0         0        0  
10        0      1    0      0         0        1  
11        0      0    0      0         1        0  
12        1      1    0      0         0        0

## Schritt 4: Diskretisieren

Eventuell enthält die Spalte 'ratings' Bewertungen mit halben Sternen, d.h. 3.5 oder 4.5. Du siehst das, wenn du dir y in der vorangegangenen Codezelle ausgeben lässt. Die Funktion der KNN-Klassifikation von python kann nur mit ganzzahligen Klassen arbeiten. Daher müssen wir Einträge der Spalte 'ratings' ganzzahligen Werten zuordnen. Wir können entweder runden, oder eine python-Funktion verwenden, die automatisch ganzzahlige Klassen zuordnet. Im zweiten Fall müssen wir die Vorhersagen wieder zurück interpretieren, also aus den ganzzahligen Klassen wieder die Bewertungen auslesen. Führe die Variante aus, die du nutzen möchtest.

### Achtung: Führe nur eine der beiden Varianten aus!

### Variante: Runden

In [5]:
y_ganzzahlig = y.astype(int)

### Variante: python Funktion

In [5]:
from sklearn import preprocessing
from sklearn import utils

lab = preprocessing.LabelEncoder()
y_transformed = lab.fit_transform(y)
print(y_transformed)
print(y.to_list())

[1 2 1 2 0 1 1 2 2 2 2 1 2]
[4.0, 5.0, 4.0, 5.0, 3.0, 4.0, 4.0, 5.0, 5.0, 5.0, 5.0, 4.0, 5.0]


## Schritt 5: Modell trainieren

Nun trainieren wir das Modell auf unserem Datensatz. Du kannst angeben, wie viele nächste Nachbarn das Modell berücksichtigen soll. Wenn das Modell trainiert ist erhälst du die Ausgabe 'KNeighborsClassifier(n_neighbors=3)'.

In [6]:
from sklearn.neighbors import KNeighborsClassifier
knn = KNeighborsClassifier(n_neighbors=3)
knn.fit(X, y_transformed)

KNeighborsClassifier(n_neighbors=3)

## Schritt 6: Filmempfehlungssystem verwenden!

Wir nutzen das Empfehlungssystem, um Bewertungen für einen neuen Film zu prognostizieren.<br/>
Suche dafür einen Film aus und bestimme die Attribute dieses Films. Erstelle dazu eine Liste mit den Genrezugehörigkeiten. Hier ist ein Beispiel für einen Film gegeben, der den Genres Comedy, Romance und Musical zugeordnet wird. Die Liste aller Attribute lautet in diesem Beispiel [Action, Adventure, Sci-Fi, IMAX, Children, Comedy, Fantasy, Animation, Romance, Drama, War, Crime, Thriller, Musical]. Sie hängt davon ab, welche Genres dein Datensatz hat. Schaue dafür in der Tabelle nach und passe den Code an.

In [7]:
neuer_film = {"Action": [0],"Adventure": [0],"Sci-Fi": [0],"IMAX": [0],"Children": [0],"Comdey": [1],"Fantasy": [0],"Animation": [0],"Romance": [1],"Drama": [0],"War": [0],"Crime": [0],"Thriller": [0],"Musical": [1]}

In [8]:
film = pd.DataFrame(neuer_film)
film

Action  Adventure  Sci-Fi  IMAX  Children  Comdey  Fantasy  Animation  \
0       0          0       0     0         0       1        0          0   

   Romance  Drama  War  Crime  Thriller  Musical  
0        1      0    0      0         0        1

Hier wird eine Bewertung vorhergesagt. Führe die zweite Codezelle nur aus, wenn du die Version python Funktion gewählt hast, um die Vorhersage wieder zu decodieren, also als Bewertung ausgeben zu lassen.

In [9]:
knn.predict(film)

array([1], dtype=int64)

In [10]:
lab.inverse_transform(knn.predict(film))

array([4.])